In [1]:
import os; os.chdir('..')

In [4]:
import pandas as pd

from datasets import Dataset, load_dataset

In [6]:
df= pd.read_csv('data/AI_checker_remade.csv')


df.sample(10)

Paragraph  AI_generated
68451   Anoop Bikram Shahi (also Anup Bikram Shahi) (N...             0
51106   The Olympus scandal was precipitated on 14 Oct...             0
102697  Leslie Herbert "Speedy" Duncan (August 10, 194...             0
97245   Elaine Rochelle Sisman (born January 20, 1952)...             1
276647  Typhoon Pamela was a powerful typhoon that str...             0
24973   Bernard Hartmut Breslauer (1 July 1918 – 14 Au...             0
277295  Rwamagana is a city and capital of both the Rw...             0
63059   Sir Lewis Cohen (23 December 1849 – 5 December...             1
19267   SN 2005gl was a supernova in the barred-spiral...             0
239340  Sulgrave Manor, Sulgrave, Northamptonshire, En...             0

In [7]:
df.rename(columns={
    "Paragraph": "text", 
    "AI_generated": "label"
}, 
          inplace=True
)

df.sample(10)

text  label
103386  Huang Yu-chun (born 16 November 1939 in Shanto...      0
13297   John Kane (7 April 1921 – 27 February 2002) wa...      1
65718   Vasiliev equations are formally consistent gau...      0
63724   Lauderdale Oval or Lauderdale Sports Ground \n...      1
86145   Earl Zebedee Hooker (January 15, 1930 – April ...      0
152381  Agnes Strickland (18 July 1796 – 8 October 185...      1
201492  Prinsep may mean any of several notable member...      0
159645  Jana Herzen  is a singer-songwriter with a foc...      1
7977    Cincy Blues Fest is an annual blues music fest...      0
261224  Bitti Mohanty, also called Bitihotra Mohanty i...      0

In [6]:
# df_dict= df.to_dict()
# df_dict

In [10]:
Dataset.from_pandas(df)

Dataset({
    features: ['text', 'label'],
    num_rows: 300000
})

In [11]:
dataset_df= Dataset.from_pandas(df)
dataset_df

Dataset({
    features: ['text', 'label'],
    num_rows: 300000
})

In [14]:
dataset_df

Dataset({
    features: ['text', 'label'],
    num_rows: 300000
})

In [15]:
# df_dict.keys()

In [23]:
# dataset_df[:10]

In [24]:
new_data= dataset_df.train_test_split(test_size=0.2)
new_data

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 240000
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 60000
    })
})

In [10]:
new_data['test'][10]

{'text': 'The Hillbrow Tower (formerly JG Strijdom Tower) is a luxury residential skyscraper located in the Hillbrow district of Johannesburg, South Africa. The tower was completed in 2006 and has 48 floors. It is the tallest residential building in Johannesburg and South Africa.\n\nThe tower is named after JG Strijdom, the first Prime Minister of South Africa. The tower has been controversial since its inception, as it has been accused of being an eyesore and a symbol of inequality in Johannesburg.',
 'label': 1}

In [25]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

In [26]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [27]:
tokenized_df = new_data.map(preprocess_function, batched=True)

Map: 100%|██████████| 60000/60000 [00:15<00:00, 3767.88 examples/s]


In [28]:
# from transformers import DataCollatorWithPadding

# data_collator = DataCollatorWithPadding(tokenizer=tokenizer, return_tensors="tf")




from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

2023-10-06 10:06:53.343215: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-10-06 10:06:55.238543: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [29]:
import evaluate

accuracy = evaluate.load("accuracy")

In [30]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

In [31]:
id2label = {0: "NEGATIVE", 1: "POSITIVE"}
label2id = {"NEGATIVE": 0, "POSITIVE": 1}

In [32]:
# from transformers import create_optimizer
# import tensorflow as tf

# batch_size = 16
# num_epochs = 5
# batches_per_epoch = len(tokenized_df["train"]) // batch_size
# total_train_steps = int(batches_per_epoch * num_epochs)
# optimizer, schedule = create_optimizer(init_lr=2e-5, num_warmup_steps=0, num_train_steps=total_train_steps)

In [33]:
# # from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

# # model = AutoModelForSequenceClassification.from_pretrained(
# #     "distilbert-base-uncased", num_labels=2, id2label=id2label, label2id=label2id
# # )

# from transformers import TFAutoModelForSequenceClassification

# model = TFAutoModelForSequenceClassification.from_pretrained(
#     "distilbert-base-uncased", num_labels=2, id2label=id2label, label2id=label2id
# )

In [34]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    "distilbert-base-uncased", num_labels=2, id2label=id2label, label2id=label2id
)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'pre_classifier.weight', 'pre_classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [35]:
# tf_train_set = model.prepare_tf_dataset(
#     tokenized_df["train"],
#     shuffle=True,
#     batch_size=16,
#     collate_fn=data_collator,
# )

# tf_validation_set = model.prepare_tf_dataset(
#     tokenized_df["test"],
#     shuffle=False,
#     batch_size=16,
#     collate_fn=data_collator,
# )

In [36]:
# import tensorflow as tf

# model.compile(optimizer=optimizer)  # No loss argument!

In [38]:
training_args = TrainingArguments(
    output_dir="my_awesome_model",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=2,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    # push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_df["train"],
    eval_dataset=tokenized_df["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=30000, training_loss=0.018804504087567328, metrics={'train_runtime': 5119.9395, 'train_samples_per_second': 93.751, 'train_steps_per_second': 5.859, 'total_flos': 4.559380077797894e+16, 'train_loss': 0.018804504087567328, 'epoch': 2.0})

In [37]:
# from transformers.keras_callbacks import KerasMetricCallback

# metric_callback = KerasMetricCallback(metric_fn=compute_metrics, eval_dataset=tf_validation_set)

In [30]:
# callbacks = [metric_callback]

In [39]:
tokenizer.save_pretrained("models/tokenizer_v1")
model.save_pretrained("models/trained_model_v1")

tokenizer.save_pretrained("models/trained_model_v11")
model.save_pretrained("models/trained_model_v11")

('models/tokenizer_v1/tokenizer_config.json',
 'models/tokenizer_v1/special_tokens_map.json',
 'models/tokenizer_v1/vocab.txt',
 'models/tokenizer_v1/added_tokens.json',
 'models/tokenizer_v1/tokenizer.json')